---

# TP 1 : Interpolation polynômiale

<b>Polytech Sorbonne, Main 3</b><br>
Analyse numérique et EDO<br>
Auteur : Fabien Vergnet

---

## Table des matières

- [Exercice 1 : Interpolation de Lagrange par différences divisées](#diffdiv)
- [Exercice 2 : Phénomène de Runge](#runge)
- [Exercice 3 : Points de Tchebychev vs points équidistants](#tcheby)
- [Exercice 4 : Interpolation de Lagrange par inversion de système linéaire](#invsyslin)
- [Exercice 5 : Interpolation de Hermite](#hermite)


In [ ]:
import numpy as np                # Librairie pour le calcul scientifique
import matplotlib.pyplot as plt   # Librairie graphique


<a id="diffdiv"></a>
## Exercice 1 : Interpolation de Lagrange par différences divisées

Dans cet exercice, on veut construire un script d’interpolation mettant en oeuvre la formule de Newton pour le calcul des coefficients du polynôme d’interpolation de Lagrange $p_n$ d’une fonction $f$ aux points $(\xi_i)_{1 \leq i \leq n+1}$, et l’algorithme d’Horner pour l’évaluation de celui-ci.

1. Définir une fonction `diffdiv` qui, à partir d’un vecteur $\xi = (\xi_i)$ et un vecteur $y = (f(\xi_i))_{1\leq i \leq n+1}$ rend un vecteur $d = (d_i)_{1 \leq i \leq n+1}$, avec $d_i = f[\xi_1, \dots , \xi_i]$. On rappelle l’algorithme vu en cours :

    - pour $i$ de 1 à $n+1$ : $d_i = f(\xi_i)$,
    - pour $k$ de 2 à $n+1$ :
        - pour i de $n+1$ à $k$ : $d_i \leftarrow \dfrac{d_i - d_{i-1}}{\xi_i - \xi_{i-k+1}}$.  
        
  Pour tester la fonction, on pourra utiliser le polynôme d'interpolation de Newton de la fonction $f(x)=\sin \left( \frac{\pi}{4}x \right)$ aux points $\{0,1,2\}$.
        
  **Attention, on rappelle que les indices des tableaux commence à 0 en Python !**

In [ ]:
### BEGIN SOLUTION
# Première version avec deux boucles
def diffdivSeq(xi, y):
    d = y.copy()
    for k in range(1,xi.size):
        for i in range(xi.size-1,k-1,-1):
            d[i] = (d[i]-d[i-1])/(xi[i]-xi[i-k])
    return d

# Deuxième version vectorielle (avec une seule boucle)
def diffdiv(xi,y):
    d = y.copy()
    for i in range(1,xi.size):
        d[i:] = (d[i:]-d[i-1:-1])/(xi[i:]-xi[:-i])
    return d

# Je teste la fonction

def f(x):
    return np.sin(np.pi*x*.25)

xi = np.array([0,1,2])
d = diffdivSeq(xi,f(xi))
e = diffdiv(xi,f(xi))
print(np.allclose(d,e))
print(d)
###  END SOLUTION

2. Définir une fonction `Horner0` qui prend en argument :
 - un vecteur de coefficients de taille $n+1$, $d = (d_i)_{1\leq i \leq n+1}$ (les différences divisées),
 - un vecteur de points d'interpolation de taille $n+1$, $\xi = (\xi_i)_{1\leq i \leq n+1}$,
 - un réel $x$,
 
 et qui retourne la valeur du polynôme $p_n$ d'interpolation de Newton aux points $(\xi_i)$, évalué au point $x$, en utilisant l'algorithme de Horner :
 
 - On pose $p = d_{n+1}$,
 - Pour $k$ allant de $n$ à 1 :
     $p \leftarrow d_k + (x-\xi_k)p$.

In [ ]:
def Horner0(d,xi,x):
    ### BEGIN SOLUTION
    p = d[-1]
    for k in range(xi.size-2,-1,-1):
        p = d[k] + (x-xi[k])*p
    return p
    ### END SOLUTION

### BEGIN SOLUTION
# Je teste la fonction
h = Horner0(np.arange(1,4),np.linspace(-1,1,3),0)
print(h)
### END SOLUTION

3. Définir une fonction `Horner` qui étend la fonction Horner0 lorsque $x$ est un vecteur. La fonction rendra donc un vecteur de même taille que $x$.

In [ ]:
def Horner(d,xi,x):
    ### BEGIN SOLUTION
    p = np.zeros(x.size)
    for i in range(x.size):
        p[i] = Horner0(d,xi,x[i])
    return p
    ### END SOLUTION

### BEGIN SOLUTION
# Je teste la fonction
h = Horner0(np.arange(1,4),np.linspace(-1,1,3),np.linspace(-1,1,5))
print(h)


# Ci-dessous, une version vectorielle plus directe (sans utiliser Horner0) 
def Hornervec(d,xi,x):
    p = np.ones(x.size)*d[-1]
    for k in range(xi.size-2,-1,-1):
        p = d[k] + (x-xi[k])*p
    return p
### END SOLUTION

4. Soit $f$ un fonction de $\mathbb{R}$ dans $\mathbb{R}$. À partir des fonctions Python précédentes, définir une fonction `interpnewton` qui prend en argument :
 - un vecteur de points d'interpolations de taille $n+1$, $\xi = \xi_{1 \leq n+1}$,
 - le vecteur des valeurs de la fonction $f$ aux points d'interpolation, de taille $n+1$, $y = (f(\xi_i))_{1\leq i \leq n+1}$,
 - un vecteur de points de taille $m$, $x=(x_i)_{1\leq i \leq m}$,
 
 et qui retourne le vecteur de taille $m$ contenant les valeurs du polynôme interpolateur de Newton aux points d'interpolation $(\xi_i)$, évalué aux points $(x_i)$.

In [ ]:
def newtoninterp(xi,y,x):
    ### BEGIN SOLUTION
    d = diffdiv(xi,y)
    p = Hornervec(d,xi,x)
    return p
    ### END SOLUTION

# Je teste la fonction à la question suivante

5. Tester cet algorithme pour interpoler la fonction $f(x)=\sin(2x^2)$.

In [ ]:
### BEGIN SOLUTION
def f(x):
    return np.sin(2*x**2)
n = 4
x = np.linspace(0,1,100)
xi = np.linspace(0,1,n)
y = f(xi)
p = newtoninterp(xi,y,x)

plt.figure(figsize=[10,6])
plt.plot(x,f(x),label="$f$")
plt.plot(x,p,label="$p_n$")
plt.legend()
plt.show()
### END SOLUTION

<a id="runge"></a>
## Exercice 2 : Phénomène de Runge

Soit f définie par $f(x) = \dfrac{1}{1+x^2}$.
1. Sur $[-5,5]$, représenter le graphe de $f$ et celui de son polynome d’interpolation de Lagrange pour le choix de points équidistant.
On fera augementer la valeur de $n$.
Qu’observe-t-on ?

In [ ]:
### BEGIN SOLUTION
def f(x):
    return 1/(1+x**2)

n = 13
xu = np.linspace(-5,5,n+1)
# xT = pointsTcheby(-5,5,n)

x = np.linspace(-5,5,100)
pu = newtoninterp(xu,f(xu),x)
# pT = newtoninterp(xT,f(xT),x)

plt.figure(figsize=[15,9])
plt.plot(x,f(x),label='$f=1./(1+x^2)$')
plt.plot(x,pu,label='$p_{}$ (uniforme)'.format(n))
plt.plot(xu,f(xu),"o",label="points d'interpolation uniforme")
# plt.plot(x,pT,label='$p_{}$ (Tchebychev)'.format(n))
# plt.plot(xT,f(xT),"s",label="points d'interpolation Tchebychev")
plt.legend()
plt.title('Phénomène de Runge')
plt.show()
### END SOLUTION

2. Représenter l’évolution de l’erreur $\|f-p_n\|_{\infty}$ en fonction de $n$. On utilisera une échelle logarithmique avec la fonction `plt.loglog`.

In [ ]:
# Pour accéder à l'aide de la fonction plt.loglog
# On pourra décommenter la ligne ci-dessous et 
# éxecuter la cellulr
#
#?plt.loglog

### BEGIN SOLUTION
N = np.arange(3,30)
erru = np.zeros(N.size)
errT = np.zeros(N.size)
x = np.linspace(-5,5,100)
y = f(x)
for i in range(N.size):
    xu = np.linspace(-5,5,N[i]+1)
    # xT = pointsTcheby(-5,5,N[i])

    pu = newtoninterp(xu,f(xu),x)
    # pT = lagrangeinterp(xT,f(xT),x)
    
    erru[i] = np.max(pu-y)
    # errT[i] = np.max(pT-y)

plt.figure(figsize=[10,6])
plt.loglog(N,erru,label="uniforme")
# plt.loglog(N,errT,label="Tchebychev")
plt.legend()
plt.title("Erreur d'interpolation en fonction du degré $n$")
plt.show()
### END SOLUTION

<a id="tcheby"></a>
## Exercice 3 : Points de Tchebychev vs points équidistants

Le but est ici de comparer le terme $N_{n+1}(x) = \prod_{k=1}^{n+1}{(x-\xi_k)}$ intervenant dans l’erreur d’interpolation,
pour des points équidistants et des points de Tchebychev.
1. Écrire une fonction `pointsTcheby` qui prend en arguments deux réels $a$ et $b$ et un entier $n$ et qui rend le vecteur des $n+1$ points de Tchebychev sur l’intervalle $[a, b]$. Les points de Tchebychev sont
définis par 

$$
\xi_{i,n}^T = \frac{a+b}{2} + \frac{b-a}{2}\cos\left( \frac{(2i-1)\pi}{2(n+1)} \right), ~~ \forall 1\leq i \leq n+1.
$$



In [ ]:
def pointsTcheby(a,b,n):
    ### BEGIN SOLUTION
    i = np.arange(1,n+2)
    x = .5*(a+b) + .5*(b-a)*np.cos((2*i-1)*np.pi/(2*(n+1)))
    return x
    ### END SOLUTION

### BEGIN SOLUTION
# Pour tester la fonction, je prend a=-1, b=1 et n=10  
# et je vérifie que mes points sont répartis de façon symmétrique
# autour de 0 et qu´il sont plus densement répartis proche des
# bords de l'intervalle
x = pointsTcheby(-1,1,10)
plt.plot(x,np.zeros(x.size),'b+')
plt.title("Répartition des points de Tchebychev")
plt.show()
print(x)
### END SOLUTION

2. Écrire une fonction `funcN` qui à partir d'un vecteur $x$ et d’un vecteur $\xi = (\xi_i)_{0\leq i \leq n}$ rend le
vecteur $N_{n+1}(x)$. On pourra utiliser la fonction `np.prod` de la librairie numpy.

In [ ]:
# La fonction np.prod prend en argument un tableau numpy er
# retourne le produit de tous ces éléments
# Pour avoir de l'aide sur cette fonction on peut décommenter
# la ligne ci dessous et éxecuter la cellule
# 
#?np.prod

def funcN(x,xi):
    ### BEGIN SOLUTION
    N = np.zeros(x.size)
    for i in range(x.size):
        N[i] = np.prod(x[i]-xi)
    return N
    ### END SOLUTION

### BEGIN SOLUTION
# Je teste la fonction
# On observe qu'elle s'annulle aux points (xi)
# ce qui est cohérent avec la formule et nous
# donne un critère de validation de la fonction
x = np.linspace(-1,1,16)
xi = np.linspace(-1,1,4)
N = funcN(x, xi)
plt.plot(xi,np.zeros(xi.size),"+")
plt.plot(x,N)
plt.title("Graphe de $N_{n+1}$")
plt.show()
### END SOLUTION

3. Tracer sur un même graphique (légendé) la fonction $x\to |N_{n+1}(x)|$ sur l’intervalle $[−1, 1]$ pour les points de Tchebychev d’une part et des points équidistants d’autre part, avec $n = 5$ puis $n = 8$. On pourra utiliser la fonction `np.abs` pour le calcul de la valeur absolue. Que constate-t-on ?

In [ ]:
### BEGIN SOLUTION
n = 8
plt.figure(figsize=[10,6])
x = np.linspace(-1,1,100)
xu5 = np.linspace(-1,1,n+1)
Nu5 = funcN(x,xu5)
xT5 = pointsTcheby(-1,1,n)
NT5 = funcN(x,xT5)
plt.plot(x,np.abs(Nu5),label="Uniforme")
plt.plot(x,np.abs(NT5),label="Tchebychev")
plt.title("Graphe de la fonction $|N_{n+1}|$ avec différents points d'interpolation")
plt.legend()
plt.show()
### END SOLUTION

4. Reprendre les questions 1 et 2 de l'exercice 2 et comparer les résultats en utilisant cette fois des points d'interpolation de Tchebychev.

In [ ]:
### BEGIN SOLUTION
def f(x):
    return 1/(1+x**2)

n = 10
xu = np.linspace(-5,5,n+1)
xT = pointsTcheby(-5,5,n)

x = np.linspace(-5,5,100)
pu = newtoninterp(xu,f(xu),x)
pT = newtoninterp(xT,f(xT),x)

plt.figure(figsize=[15,9])
plt.plot(x,f(x),label='$f=1./(1+x^2)$')
plt.plot(x,pu,label='$p_{}$ (uniforme)'.format(n))
plt.plot(xu,f(xu),"o",label="points d'interpolation uniforme")
plt.plot(x,pT,label='$p_{}$ (Tchebychev)'.format(n))
plt.plot(xT,f(xT),"s",label="points d'interpolation Tchebychev")
plt.legend()
plt.title('Phénomène de Runge')
plt.show()
### END SOLUTION

In [ ]:
### BEGIN SOLUTION
N = np.arange(3,30)
erru = np.zeros(N.size)
errT = np.zeros(N.size)
x = np.linspace(-5,5,100)
y = f(x)
for i in range(N.size):
    xu = np.linspace(-5,5,N[i]+1)
    xT = pointsTcheby(-5,5,N[i])

    pu = newtoninterp(xu,f(xu),x)
    pT = newtoninterp(xT,f(xT),x)
    
    erru[i] = np.max(pu-y)
    errT[i] = np.max(pT-y)

plt.figure(figsize=[10,6])
plt.loglog(N,erru,label="uniforme")
plt.loglog(N,errT,label="Tchebychev")
plt.legend()
plt.title("Erreur d'interpolation en fonction du degré $n$")
plt.show()
### END SOLUTION

<a id="invsyslin"></a>
## Exercice 4 : Interpolation de Lagrange par inversion de système linéaire
1. Définir une fonction `polyval` qui prend en argument :
 - un vecteur de points de taille $n$, $x = (x_i)_{0 \leq i < n}$,
 - un tableau de coefficients polynômiaux de taille $m$, $a = (a_i)_{0\leq i < m}$, 
 
  et qui retourne un tableau de taille $n$ contenant les évaluations aux points $(x_i)_{0\leq i\leq n}$ du polynôme $p$ défini par $$ p(x) = a_0 + a_1 x + \dots + a_m x^m, ~~~~\forall x\in\mathbb{R}.$$

  Tester la fonction en traçant sur la même figure les graphes des polynômes $p_1(x)= 5*x^2 + 2$ et $p_2(x)= 0.1*x^4 + 3x^2$ sur l'intervalle $[-10,10]$.

In [ ]:
def polyval(x,a):
    ### BEGIN SOLUTION
    y = np.zeros(x.size)
    for i in range(a.size):
        for j in range(x.size):
            y[j] += a[i]*x[j]**i
    return y
    ### END SOLUTION

### BEGIN SOLUTION
# Pour vérifier la fonction polyval, je trace les graphes de polynomes p_1 et p_2.
# Je n'oublie pas d'ajouter un titre et une légende

x = np.linspace(-10,10,100)
p1 = polyval(x,np.array([2,0,5]))
p2 = polyval(x,np.array([0,0,3,0.1]))
plt.plot(x,p1,label='$p_1$')
plt.plot(x,p2, label='$p_2$')
plt.legend(loc='lower right')
plt.title("Graphe des polynômes $p_1$ et $p_2$")
plt.show()

# On peut également définir une version vectorielle pour cette fonction
def polyvalVec(x,a):
    y = np.zeros(x.size)
    for i in range(a.size):
        y += a[i]*x**i
    return y

# A titre d'information, on peut comparer les vitesses d'éxecution des deux fonctions
x2 = np.linspace(0,1,1000)
%timeit polyval(x2,np.array([2,0,5]))
%timeit polyvalVec(x2,np.array([2,0,5]))
### END SOLUTION

2. Définir une fonction `buildmatrix` qui à partir d’un vecteur de points de taille $n + 1$, $\xi = (\xi_i)_{0\leq i \leq n}$, retourne la matrice $V$ à determiner dans l’exercice 3 de la feuille de TD 1.

In [ ]:
def buildmatrix(xi):
    ### BEGIN SOLUTION
    V = np.zeros((xi.size,xi.size))
    for i in range(xi.size):
        for j in range(xi.size):
            V[i,j] = xi[i]**j
    return V
    ### END SOLUTION

### BEGIN SOLUTION
# On peut également définir une version "à la numpy" pour la fonction buildmatrix
def buildmatrixNumpy(xi):
    V = np.array([[xi[i]**j for j in range(xi.size)] for i in range(xi.size)])
    return V

# Je teste ces deux fonctions
xi = np.array([1,2,3])
v = buildmatrix(xi)
print(v)
v = buildmatrixNumpy(xi)
print(v)

# A titre d'information, on peut comparer les vitesses d'éxecution des deux fonctions
#xi2 = np.linspace(0,1,1000)
#%timeit buildmatrix(xi2)
#%timeit buildmatrixNumpy(xi2)
### END SOLUTION

3. Définir une fonction `solvelagrangesystem` qui à partir de deux vecteurs $\xi$ et $y$ (de même taille $n+1$) calcule les coefficients polynomiaux du polynôme $p_n$ d’interpolation de Lagrange aux points $(\xi_i, y_i)$ pour tout $i \in \{0,\dots,n\}$. 

  On pourra utiliser la fonction `np.linalg.solve(V,y)` pour mettre en oeuvre la résolution du système linéaire $Va = y$, où $a$ est le tableau contenant les coefficients polynomiaux de $p_n$.

In [ ]:
def solvelagrangesystem(xi,y):
    ### BEGIN SOLUTION
    V = buildmatrix(xi)
    a = np.linalg.solve(V,y)
    return a
    ### END SOLUTION

### BEGIN SOLUTION
# Pour tester la fonction, je choisi un vecteur y aléatoirement avec la fonction np.random.rand
y = np.random.rand(xi.size)
# J'appelle la fonction solvelagrangesystem
a = solvelagrangesystem(xi,y)
# Pour vérifier le résultat, je check que le polynome obtenu vaut bien y[i] au point x[i]
# Pour cela j'utilise la fonction polyval et la fonction np.allclose qui rend "True" si l'élément p[i] du vecteur p ci-dessous est égal à y[i] (à l'erreur machine près) 
p = polyval(xi,a)
print(np.allclose(p,y))
### END SOLUTION

4. Soit $f$ une fonction de $\mathbb{R}$ dans $\mathbb{R}$. En utilisant les fonctions Python `solvelagrangesystem` et `polyval`, définir une fonction `lagrangeinterp` qui prend en argument :
  - un vecteur de points d'interpolations de taille $n+1$, $\xi = \xi_{1 \leq n+1}$,
  - le vecteur des valeurs de la fonction $f$ aux points d'interpolation, de taille $n+1$, $y = (f(\xi_i))_{1\leq i \leq n+1}$,
  - un vecteur de points de taille $m$, $x=(x_i)_{1\leq i \leq m}$,
 
  et qui retourne le vecteur de taille $m$ contenant les valeurs du polynôme interpolateur de Lagrange aux points d'interpolation $(\xi_i)$, évalué aux points $(x_i)$.

In [ ]:
def lagrangeinterp(xi,y,x):
    ### BEGIN SOLUTION
    a = solvelagrangesystem(xi,y)
    p = polyvalVec(x,a)
    return p
    ### END SOLUTION

### BEGIN SOLUTION
# Pour tester cette fonction, je vais interpoler la fonction f(x)=3*x+2 aux points -1 et 1
# Comme f est un polynome de degré 1, son polynome interpolateur de Lagrange en deux points et aussi un polynome de degré 1
# Le polynome interpolateur de Lagrange est donc forcément égal à f
xi = np.array([-1,1])
y = 3*xi+2
x = np.linspace(0,1,100)
p = lagrangeinterp(xi,y,x)
# Et on vérifie que p[i] et bien égal à 3*x[i]+2 pour tout i
print(np.allclose(p,3*x+2))
### END SOLUTION

5. Soit $f(x) = sin(2x^2)$. Déterminer le polynôme d'interpolation de Lagrange de $f$ pour $n+1$ points uniformément répartis sur $[0, 1]$. 

  Tracer sur une même figure les graphes de la fonction $f$ et du polynôme $p_n$ en les évaluant sur un maillage plus fin (prendre par exemple 100 points). 
  
  Faire varier le nombre de points $n$ pour comparer. Prendre, par exemple $n=2$, $n=3$, $n=4$.

In [ ]:
### BEGIN SOLUTION
N = 10
xi = np.linspace(0,1,N+1)

def f(x):
    return np.sin(2*x**2)

x = np.linspace(0,1,4*(N+1))
p = lagrangeinterp(xi,f(xi),x)

plt.figure(figsize=[10,5])
plt.plot(xi,f(xi),'k+')
plt.plot(x,f(x),'b-',label='$f$')
plt.plot(x,p,'r--',label='$p_n$')
plt.title("La fonction $f$ et son polynôme interpolateur de Lagrange")
plt.legend()
plt.show()

# Je n'oublie par donner un titre et une légende à ma figure
### END SOLUTION

6. Comparer la performance de cet algorithme avec la méthode utilisée dans l’exercice 1. On pourra utiliser la syntaxe `%timeit` en début de ligne pour obtenir le temps d'évaluation des commandes.

In [ ]:
### BEGIN SOLUTION
%timeit p = newtoninterp(xi,f(xi),x)

def newtoninterpSeq(xi,y,x):
    d = diffdivSeq(xi,y)
    p = Horner(d,xi,x)
    return p

%timeit p = newtoninterpSeq(xi,f(xi),x)
### END SOLUTION

In [ ]:
### BEGIN SOLUTION
%timeit p = lagrangeinterp(xi,f(xi),x)

def lagrangeinterpSeq(xi,y,x):
    a = solvelagrangesystem(xi,y)
    p = polyval(x,a)
    return p

%timeit p = lagrangeinterpSeq(xi,f(xi),x)
### END SOLUTION

=== BEGIN RESPONSE ===

**Réponse :**
On remarque (sur mon ordinateur en tout cas...) que la méthode utilisant la forme de Newton et l'algorithme de Horner vectoriel est l'algorithme le plus efficace.
La méthode de l'exercice 1 avec la fonction polyval vectorielle est derrière en terme de performance de calcul.
Par contre, les version séquentilles de ces algotithme sont beaucoup plus lentes.

=== END RESPONSE ===

<a id="hermite"></a>
## Exercice 3 : Interpolation de Hermite

1. Déterminer (à la main) les polynômes $h_0$, $h_1$, $h_2$, $h_3$ vérifiant

  $$h_0(0)=1, ~ h_0^{\prime}(0) = 0, ~ h_0(1) = 0, ~ h_0^{\prime}(1) = 0,$$ 

  $$h_1(0)=0, ~ h_1^{\prime}(0) = 1, ~ h_1(1) = 0, ~ h_1^{\prime}(1) = 0,$$ 

  $$h_2(0)=0, ~ h_2^{\prime}(0) = 0, ~ h_2(1) = 1, ~ h_2^{\prime}(1) = 0,$$ 

  $$h_3(0)=0, ~ h_3^{\prime}(0) = 0, ~ h_3(1) = 0, ~ h_3^{\prime}(1) = 1.$$ 

  Définir ensuite les fonctions Python correspondantes.
  
 === BEGIN RESPONSE ===
 
 Pour chaque polynôme à déterminer nous avons 4 équations. On cherche donc un polynôme de degré 3 (4 coefficients), afin que le système linéaire admette une unique solution.
 
 === END RESPONSE ===

In [ ]:
### BEGIN SOLUTION
def h0(x):
    return 2*x**3 -3*x**2 + 1

def h1(x):
    return x**3 - 2*x**2 + x

def h2(x):
    return -2*x**3 + 3*x**2

def h3(x):
    return x**3 - x**2
### END SOLUTION

2. On considère une fonction $f$ de classe $\mathcal{C}^1$ sur $[0,1]$. Montrer que le polynôme $q$ de $\mathcal{P}^3$ vérifiant

  $$q(0) = f(0), ~~~~~q^\prime(0) = f^\prime(0), ~~~~~q(1) = f(1), ~~~~~q^\prime(1) = f^\prime(1),$$

  s'écrit sous la forme $$q(x) = f(0)h_0(x) + f^\prime(0)h_0(x) + f(1)h_2(x) + f^\prime(1)h_3(x).$$
  
3. Définir une fonction `hermiteinterp` qui prend en argument :
  - une fonction $f$,
  - sa dérivée $f^\prime$,
  - un vecteur de points $x = (x_i)_{1\leq i\leq n}$ de taille $n$,
  
  et qui retourne le polynôme d'interpolation de Hermie aux points 0 et 1, évalué aux points $(x_i)$.

In [ ]:
def hermiteinterp(f,fprime,x):
    ### BEGIN SOLUTION
    p = f(0)*h0(x) + fprime(0)*h1(x) + f(1)*h2(x) + fprime(1)*h3(x)
    return p
    ### END SOLUTION

# Je teste la fonction à la question suivante

4. Comparer l’interpolation obtenue grâce à $q$ et au polynôme de Lagrange $p_3$ associés à des points équidistants sur $[0, 1]$ pour la fonction $f(x) = \sin(2x^2)$, et d’autres fonctions de votre choix.

In [ ]:
### BEGIN SOLUTION
def f(x):
    return np.sin(2*x**2)
def fprime(x):
    return 4*x*np.cos(2*x**2)

x = np.linspace(0,1,100)
q = hermiteinterp(f,fprime,x)
xi = np.linspace(0,1,4)
p3 = lagrangeinterp(xi,f(xi),x)

plt.plot(x,f(x),label='$f$')
plt.plot(x,q,label='$q$')
plt.plot(x,p3,label='$p_3$')
plt.legend()
plt.show()
### END SOLUTION